# Consumed emissions 

* Example of consumed emissions calculation, with comparison of our generation data to 930 generation data

In [1]:
import plotly.express as px
import os
import pandas as pd
import numpy as np
import missingno as msno

In [2]:
%reload_ext autoreload
%autoreload 2

# Tell python where to look for modules. 
# Depending on how your jupyter handles working directories, this may not be needed.
import sys
sys.path.append('../../hourly-egrid/')

from src.consumed import HourlyBaDataEmissionsCalc, get_average_emission_factors
from src.load_data import ba_timezone
import src.data_cleaning as data_cleaning

/Users/gailin.pease/miniconda3/envs/hourly_egrid/lib/python3.9/site-packages/geopandas/_compat.py:106: UserWarning: The Shapely GEOS version (3.9.1dev-CAPI-1.14.1) is incompatible with the GEOS version PyGEOS was compiled with (3.9.1-CAPI-1.14.2). Conversions between both will be slow.
  warnings.warn(


2022-06-09 12:42:31,281 - pudl.workspace.setup - INFO - PUDL user settings file .pudl.yml not found.
2022-06-09 12:42:31,281 - pudl.workspace.setup - INFO - PUDL user settings file .pudl.yml not found.


In [3]:
from gridemissions.emissions import BaDataEmissionsCalc
from gridemissions.load import BaData

In [8]:
cleaned = BaData("../data/eia930/chalendar/EBA_adjusted_elec.csv")

In [10]:
consumed_calc = BaDataEmissionsCalc(cleaned)

In [ ]:
consumed_calc.process()

In [13]:
consumed_calc.pollutant_data.df.head()

CO2_AEC_NG   CO2_AECI_NG  CO2_AESO_NG  \
2018-07-01 00:00:00+00:00  722837.946646  2.558987e+06   439.000001   
2018-07-01 01:00:00+00:00  666238.223802  2.485406e+06   439.000001   
2018-07-01 02:00:00+00:00  611888.202489  2.323381e+06   439.000000   
2018-07-01 03:00:00+00:00  533910.006339  2.111128e+06   439.000000   
2018-07-01 04:00:00+00:00  475535.196116  2.111126e+06   439.000001   

                              CO2_AVA_NG   CO2_AVRN_NG   CO2_AZPS_NG  \
2018-07-01 00:00:00+00:00  114772.657761  80514.740568  1.976384e+06   
2018-07-01 01:00:00+00:00  117471.956723  86781.607203  2.097934e+06   
2018-07-01 02:00:00+00:00  121503.630319  50087.060795  2.086198e+06   
2018-07-01 03:00:00+00:00  124344.171590  45634.827326  2.073630e+06   
2018-07-01 04:00:00+00:00   54484.881076  47041.598601  1.959990e+06   

                             CO2_BANC_NG  CO2_BCHA_NG    CO2_BPAT_NG  \
2018-07-01 00:00:00+00:00  499054.478622          4.0  335612.776671   
2018-07-01 01:00:00+00:00  493907.667789          4.0  337522.192463   
2018-07-01 02:00:00+00:00  510814.609778          4.0  340554.091374   
2018-07-01 03:00:00+00:00  513511.615818          4.0  344680.136369   
2018-07-01 04:00:00+00:00  542214.458616          4.0  347795.892060   

                           CO2_CEN_NG  ...     CO2_TEC_TI    CO2_TEPC_TI  \
2018-07-01 00:00:00+00:00  439.000005  ...  145496.799517 -195423.195261   
2018-07-01 01:00:00+00:00  439.000007  ...   76228.959440 -433556.444520   
2018-07-01 02:00:00+00:00  439.000002  ...  136407.793949 -639799.890576   
2018-07-01 03:00:00+00:00  439.000002  ...  208915.040962 -706243.568145   
2018-07-01 04:00:00+00:00  439.000015  ...  216172.862148 -199062.018616   

                            CO2_TIDC_TI  CO2_TPWR_TI     CO2_TVA_TI  \
2018-07-01 00:00:00+00:00 -32103.830319 -5155.741268 -308262.593447   
2018-07-01 01:00:00+00:00 -36644.714831 -5085.824444 -351187.559304   
2018-07-01 02:00:00+00:00 -39488.823873 -4742.032433 -272446.874341   
2018-07-01 03:00:00+00:00 -32004.958832 -4816.348165  -21187.715412   
2018-07-01 04:00:00+00:00 -23278.303706 -5015.839512  -77536.804447   

                            CO2_WACM_TI    CO2_WALC_TI   CO2_WAUW_TI  \
2018-07-01 00:00:00+00:00  1.084487e+06  131588.621217 -33848.188237   
2018-07-01 01:00:00+00:00  1.039144e+06  100696.882219 -31867.283650   
2018-07-01 02:00:00+00:00  1.061485e+06  139840.243117 -27365.557338   
2018-07-01 03:00:00+00:00  1.095513e+06  231178.509174 -28912.100148   
2018-07-01 04:00:00+00:00  1.062628e+06  246455.090351 -29542.258671   

                           CO2_WWA_TI  CO2_YAD_TI  
2018-07-01 00:00:00+00:00  768.834230  737.802770  
2018-07-01 01:00:00+00:00  639.526286  736.400549  
2018-07-01 02:00:00+00:00  881.772096 -494.425287  
2018-07-01 03:00:00+00:00  938.833025 -516.543180  
2018-07-01 04:00:00+00:00  551.944310 -453.347052  

[5 rows x 562 columns]

# Use our generation #s 

Replace each total generation column (EBA.{ba}-ALL.NG.H) with our generation for that BA and hour 

TODO: figure out if we need to edit demand to align with our generation 

note: SRC flags are used only in `_add_production_emissions`, so don't need after we rewrite to use hourly rates

In [4]:
hourly_consumed_calc = HourlyBaDataEmissionsCalc("../data/downloads/eia930/chalendar/EBA_adjusted_elec.csv")

In [ ]:
hourly_consumed_calc.process()

In [429]:
ba = "PACE"
px.line(consumed_calc.df, x=consumed_calc.df.index, y=[f'CO2_{ba}_D', f"CO2_{ba}_NG"])

In [431]:
ba = "PACE"
px.line(hourly_consumed_calc.df, x=hourly_consumed_calc.df.index, y=[f'CO2_{ba}_D', f"CO2_{ba}_NG"])